<a href="https://colab.research.google.com/github/jeremiegautreau/Topic_modeling_COP_28/blob/main/Topic_modeling_COP28.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Topic Modeling COP28

  

Recherche des thématiques des tweets en lien avec la COP28 dans le corpus

### Installation des librairies requises

In [ ]:
pip install transformers

In [ ]:
pip install sentence_transformers

In [ ]:
pip install bertopic

In [ ]:
pip install -U spacy

### Chargement des librairies pour le preprocessing

In [ ]:
import spacy.cli
spacy.cli.download("fr_core_news_md") # importation d'un modèle de langue français

✔ Download and installation successful
You can now load the package via spacy.load('fr_core_news_md')


In [ ]:
import spacy
from spacy import displacy
nlp = spacy.load('fr_core_news_md')

In [ ]:
stop_words = nlp.Defaults.stop_words
stop_words = list(stop_words)

In [ ]:
pip install demoji

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.9/42.9 kB 2.2 MB/s eta 0:00:00


In [ ]:
import pandas as pd

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


### Chargement du corpus de tweets

In [ ]:
df=pd.read_csv('/content/drive/MyDrive/network/tweetcop28prep.csv', sep = ',') # Le corpus a été au préalable nettoyer

In [ ]:
df.head()

tweet_id                                               text  \
0  1726536195315040404  Combien d'audits alimentaires et d'inspections...   
1  1725558234650407279  Bureau Veritas est fier de se classer dans la ...   
2  1704053099273306158    Meet Sophie (Australia) https://t.co/4BIctUddQx   
3  1691351519411814400  En juillet, nous avons publié nos résultats H1...   
4  1729570780705415227  Aujourd'hui, @rodolphesaade est monté sur scèn...   

  language   type  bookmark_count  favorite_count  retweet_count  reply_count  \
0       en  Tweet             1.0             5.0            2.0          0.0   
1       en  Tweet             0.0             6.0            1.0          0.0   
2       fr  Reply             0.0             3.0            0.0          0.0   
3       en  Tweet             1.0             4.0            5.0          0.0   
4       en  Tweet             0.0            25.0            8.0          3.0   

   view_count           created_at  \
0       888.0  2023-11-20 10:41:21   
1       441.0  2023-11-17 17:55:17   
2       286.0  2023-09-19 10:41:33   
3       705.0  2023-08-15 09:30:00   
4      1820.0  2023-11-28 19:39:42   

                                              client hashtags  \
0  <a href="https://mobile.twitter.com" rel="nofo...      NaN   
1  <a href="https://mobile.twitter.com" rel="nofo...      NaN   
2  <a href="https://mobile.twitter.com" rel="nofo...      NaN   
3  <a href="https://mobile.twitter.com" rel="nofo...      NaN   
4  <a href="http://twitter.com/download/iphone" r...      NaN   

                                                urls media_type  \
0                                                NaN        NaN   
1  https://group.bureauveritas.com/newsroom/burea...      photo   
2                                                NaN      photo   
3                       https://youtu.be/9KE5EZPeY0A        NaN   
4                                                NaN      photo   

                                          media_urls       username  \
0                                                NaN  bureauveritas   
1    https://pbs.twimg.com/media/F_Jp-gOWcAAp2MV.jpg  bureauveritas   
2    https://pbs.twimg.com/media/F6YDOKsXIAACZLE.jpg  bureauveritas   
3                                                NaN  bureauveritas   
4  https://pbs.twimg.com/media/GACrdPcWcAAEx1F.jp...         cmacgm   

    categorie  
0  Entreprise  
1  Entreprise  
2  Entreprise  
3  Entreprise  
4  Entreprise

In [ ]:
df.loc[:,'username'].value_counts()

### Processus de recherhces des thématiques

In [ ]:
from sentence_transformers import SentenceTransformer # sentence embeddings pour la représentation des tweets
import transformers

### Preprocessing des tweets

In [ ]:
import demoji
import re
demoji.download_codes()

In [ ]:
def remove_emoji(text):
  dem = demoji.findall(text)
  for item in dem.keys():
    text = text.replace(item, '')
  return text

In [ ]:
def preprocessing_mot(texte):
    texte = texte.replace('\n', " ") # retrait des sauts de ligne
    texte = texte.replace('@', "") # retrait des arobases
    texte = texte.replace('’', "'") # changement du caractère "’" par une apostrophe
    texte = remove_emoji(texte) # retrait des emojis


    return texte

In [ ]:
df['tweet_clean']=df['text'].apply(preprocessing_mot)

In [ ]:
tweet=df['tweet_clean'].to_list()

### Sentence embeddings des tweets

In [ ]:
embedding_model = SentenceTransformer('sentence-transformers/distiluse-base-multilingual-cased-v1')


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/341 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/2.45k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

2_Dense/config.json:   0%|          | 0.00/114 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.58M [00:00<?, ?B/s]

In [ ]:
embeddings = embedding_model.encode(tweet, show_progress_bar=True)

Batches:   0%|          | 0/380 [00:00<?, ?it/s]

### Réduction de dimensions et clustering des tweets par thématiques

In [ ]:
from umap import UMAP
from hdbscan import HDBSCAN

umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine', random_state=42)
hdbscan_model = HDBSCAN(min_cluster_size=15, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [ ]:
reduced_embeddings = UMAP(n_neighbors=15, n_components=2, min_dist=0.0, metric='cosine', random_state=42).fit_transform(embeddings)

In [ ]:
from bertopic.representation import KeyBERTInspired, MaximalMarginalRelevance

# KeyBERT
keybert = KeyBERTInspired()

# MMR
mmr = MaximalMarginalRelevance(diversity=0.3)


representation_model = {
    "KeyBERT": keybert,
    "MMR": mmr
}

In [ ]:
from bertopic import BERTopic

topic_model = BERTopic(


  embedding_model=embedding_model,
  umap_model=umap_model,
  hdbscan_model=hdbscan_model,
  representation_model=representation_model,


  language="multilingual",
  top_n_words=10,
  verbose=True
)

topics, probs = topic_model.fit_transform(tweet, embeddings)

2024-02-03 09:41:07,333 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-02-03 09:41:20,662 - BERTopic - Dimensionality - Completed ✓
2024-02-03 09:41:20,664 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-02-03 09:41:21,167 - BERTopic - Cluster - Completed ✓
2024-02-03 09:41:21,176 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-02-03 09:41:28,140 - BERTopic - Representation - Completed ✓


### Résultat de la recherche de thématiques
Attention le topic -1 n'est pas à prendre en compte. il correspond à tous les tweets qui n'ont pas pu être classé dans une thématiques.


In [ ]:
topic_model.get_topic_info()[:32]

Topic  Count                                               Name  \
0      -1   4133                                     -1_de_la_et_co   
1       0   1362          0_nucléaire_énergies_fossiles_énergétique   
2       1    326  1_agriculture_agriculteurs_agricoles_agroécologie   
3       2    267                      2_femmes_égalité_genre_filles   
4       3    266           3_eau_sécheresse_bassines_assainissement   
5       4    242                4_paris_parisiens_ville_parisiennes   
6       5    232                    5_gaza_israël_hamas_humanitaire   
7       6    223              6_uicnfrance_biodiversité_nature_uicn   
8       7    211            7_humanitaire_sif_ong_humanitaires_aide   
9       8    203                   8_électriques_véhicules_acier_gm   
10      9    189           9_chaleur_températures_vagues_changement   
11     10    161      10_alimentaire_faim_alimentaires_malnutrition   
12     11    149                          11_mer_pêche_marins_océan   
13     12    146                       12_merci_votre_soutien_grand   
14     13    137       13_catholique_secours_pauvreté_caritasfrance   
15     14    136                     14_proches_pensées_ses_famille   
16     15    129                        15_https_co_savoir_réaction   
17     16    123      16_écologique_planification_macron_transition   
18     17    121          17_afrique_sahel_muraille_greenwallafrica   
19     18    113                   18_pays_pacte_financier_dommages   
20     19    106            19_européen_europe_parlement_européenne   
21     20     89                       20_train_ticket_trains_avion   
22     21     84                    21_droite_extrême_nazis_raciste   
23     22     81        22_elisabeth_borne_ministre_première_direct   
24     23     77          23_animaux_animal_carolinerooseeu_animale   
25     24     77                     24_ukraine_poutine_kyiv_guerre   
26     25     68           25_antisémitisme_contre_juifs_république   
27     26     65                  26_climatique_rapport_climat_giec   
28     27     64                 27_wgeo_greeneconomy_go_green_gage   
29     28     61                    28_liberté_jdd_presse_rédaction   
30     29     61                29_viande_élevage_mfesneau_élevages   
31     30     58                    30_espèces_menacées_rouge_liste   

                                       Representation  \
0   [de, la, et, co, https, pour, les, le, des, nous]   
1   [nucléaire, énergies, fossiles, énergétique, é...   
2   [agriculture, agriculteurs, agricoles, agroéco...   
3   [femmes, égalité, genre, filles, droits, des, ...   
4   [eau, sécheresse, bassines, assainissement, ac...   
5   [paris, parisiens, ville, parisiennes, jeux, r...   
6   [gaza, israël, hamas, humanitaire, cessez, feu...   
7   [uicnfrance, biodiversité, nature, uicn, congr...   
8   [humanitaire, sif_ong, humanitaires, aide, per...   
9   [électriques, véhicules, acier, gm, voiture, a...   
10  [chaleur, températures, vagues, changement, cl...   
11  [alimentaire, faim, alimentaires, malnutrition...   
12  [mer, pêche, marins, océan, océans, protection...   
13  [merci, votre, soutien, grand, lt, beaucoup, f...   
14  [catholique, secours, pauvreté, caritasfrance,...   
15  [proches, pensées, ses, famille, mes, sa, cond...   
16  [https, co, savoir, réaction, article, plus, c...   
17  [écologique, planification, macron, transition...   
18  [afrique, sahel, muraille, greenwallafrica, ve...   
19  [pays, pacte, financier, dommages, sommet, per...   
20  [européen, europe, parlement, européenne, ue, ...   
21  [train, ticket, trains, avion, pass, ferroviai...   
22  [droite, extrême, nazis, raciste, néo, haine, ...   
23  [elisabeth_borne, ministre, première, direct, ...   
24  [animaux, animal, carolinerooseeu, animale, bi...   
25  [ukraine, poutine, kyiv, guerre, ukrainienne, ...   
26  [antisémitisme, contre, juifs, république, hai...   
27  [climatique, rapport, climat, giec, hc_climat,...   
28  [wg

In [ ]:
topic_model.get_topic(7)

[('humanitaire', 0.02758144641151245),
 ('sif_ong', 0.025691398054091572),
 ('humanitaires', 0.01736675813779493),
 ('aide', 0.01718714602656641),
 ('personnes', 0.015619021274686217),
 ('sif', 0.014846168960815748),
 ('ong', 0.014277810434313832),
 ('pakistan', 0.013388546562621603),
 ('co', 0.01275139392920226),
 ('https', 0.012751214608271055)]

In [ ]:
topic_model.get_topic_info().to_csv('/content/drive/MyDrive/network/topic_info_cop28.csv', sep=',', index=False)

In [ ]:
topic_model.get_document_info(tweet)

Document  Topic  \
0      Combien d'audits alimentaires et d'inspections...     10   
1      Bureau Veritas est fier de se classer dans la ...     -1   
2        Meet Sophie (Australia) https://t.co/4BIctUddQx     15   
3      En juillet, nous avons publié nos résultats H1...     -1   
4      Aujourd'hui, rodolphesaade est monté sur scène...     -1   
...                                                  ...    ...   
12146  Document - L'UE et les États-Unis soulignent e...      0   
12147  Selon ⁦ContexteEnergie⁩ ⁦rte_france⁩ a vu le n...      0   
12148        grunblatt ContexteEnergie rte_france Merci!     -1   
12149  Décryptage sur la réforme du market design en ...      0   
12150  BrunoSWAC SFENorg Le projet est sorti, mais c'...     69   

                                                Name  \
0      10_alimentaire_faim_alimentaires_malnutrition   
1                                     -1_de_la_et_co   
2                        15_https_co_savoir_réaction   
3                                     -1_de_la_et_co   
4                                     -1_de_la_et_co   
...                                              ...   
12146      0_nucléaire_énergies_fossiles_énergétique   
12147      0_nucléaire_énergies_fossiles_énergétique   
12148                                 -1_de_la_et_co   
12149      0_nucléaire_énergies_fossiles_énergétique   
12150             69_cbeaune_a69_caroledelga_travaux   

                                          Representation  \
0      [alimentaire, faim, alimentaires, malnutrition...   
1      [de, la, et, co, https, pour, les, le, des, nous]   
2      [https, co, savoir, réaction, article, plus, c...   
3      [de, la, et, co, https, pour, les, le, des, nous]   
4      [de, la, et, co, https, pour, les, le, des, nous]   
...                                                  ...   
12146  [nucléaire, énergies, fossiles, énergétique, é...   
12147  [nucléaire, énergies, fossiles, énergétique, é...   
12148  [de, la, et, co, https, pour, les, le, des, nous]   
12149  [nucléaire, énergies, fossiles, énergétique, é...   
12150  [cbeaune, a69, caroledelga, travaux, grève, so...   

                                                 KeyBERT  \
0      [alimentaires, malnutrition, alimentaire, faim...   
1      [https, climatique, ensemble, écologique, poli...   
2      [https, libres, libe, dxfhb5eiz9, gvfxfwk1qj, ...   
3      [https, climatique, ensemble, écologique, poli...   
4      [https, climatique, ensemble, écologique, poli...   
...                                                  ...   
12146  [énergétique, charbon, carbone, énergies, éner...   
12147  [énergétique, charbon, carbone, énergies, éner...   
12148  [https, climatique, ensemble, écologique, poli...   
12149  [énergétique, charbon, carbone, énergies, éner...   
12150  [routiers, projets, a69, projet, associations,...   

                                                     MMR  \
0      [alimentaire, faim, alimentaires, malnutrition...   
1      [de, la, et, co, https, pour, les, le, des, nous]   
2      [https, co, savoir, réaction, article, plus, c...   
3      [de, la, et, co, https, pour, les, le, des, nous]   
4      [de, la, et, co, https, pour, les, le, des, nous]   
...                                                  ...   
12146  [nucléaire, énergies, fossiles, énergétique, é...   
12147  [nucléaire, énergies, fossiles, énergétique, é...   
12148  [de, la, et, co, https, pour, les, le, des, nous]   
12149  [nucléaire, énergies, fossiles, énergétique, é...   
12150  [cbeaune, a69, caroledelga, travaux, grève, so...   

                                     Representative_Docs  \
0      [#COP28  Les gouvernements doivent prendre des...   
1      [C'est incroyable jusqu'où ce cours que j'ai c...   
2      [Pour plus d'infos sur les 3 contentieux en co...   
3      [C'est incroyable jusqu'où ce cours que j'ai c...   
4      [C'est incroyable jusqu'où ce cours que j'ai c...   
...                                            

In [ ]:
topic_model.get_document_info(tweet).to_csv('/content/drive/MyDrive/network/topic_doc_cop28.csv', sep=',', index=False)

In [ ]:
import numpy as np

t = np.arange(1,30)

In [ ]:
Topic_COP28 = [0, 1, 3, 6, 8, 9, 10, 11, 16, 17, 18, 19, 26, 27, 29, 30]
len(Topic_COP28)

16

### Visualisation des 31 premières thématiques

In [ ]:
topic_model.visualize_documents(tweet, topics= np.arange(0,31), reduced_embeddings=reduced_embeddings,
hide_annotations=True, hide_document_hover=False)

### Visualisations des 16 thématiques retenues

In [ ]:
topic_model.visualize_documents(tweet, topics= Topic_COP28, reduced_embeddings=reduced_embeddings,
hide_document_hover=True, title="Thématiques des tweets sur la COP28")

In [ ]:
df_topic = topic_model.get_document_info(tweet)

In [ ]:
df_merge = pd.concat([df,df_topic[['Topic', 'Name', 'Representation',  'Probability', 'Representative_document']]], axis=1)

In [ ]:
df_merge.head()

In [ ]:
df_merge.to_csv('/content/drive/MyDrive/network/topic_cop28.csv', sep=',', index=False)

### Création des fichiers des noeuds et des liens pour GEPHI

In [ ]:
Account = df_merge.loc[df_merge['Topic'].isin(Topic_COP28), 'username'].unique()

In [ ]:
 dict_acc={}

for index, element in enumerate(Account):
    dict_acc[index] = element

In [ ]:
dict_acc = {v: k for k, v in dict_acc.items()}

In [ ]:
df_edge = df_merge[['Topic', 'username', 'categorie', 'tweet_id']].loc[df_merge['Topic'].isin(Topic_COP28)].groupby(['username','categorie', 'Topic']).count().reset_index()

In [ ]:
df_edge['Id'] = df_edge['username'].map(dict_acc)+31

In [ ]:
df_edge['ratio'] = round(df_edge['tweet_id'] / df_edge.groupby('username')['tweet_id'].transform('sum')*100,0)

In [ ]:
node_user = pd.pivot_table(df_edge,
                           values=['username', 'categorie'],
                           index=['Id'],
                           aggfunc='first'
                           )
node_user.reset_index(inplace=True)

In [ ]:
node_user=node_user[['Id', 'username', 'categorie']]

In [ ]:
df_edge = df_edge[['Id', 'Topic', 'ratio']]

In [ ]:
df_edge.columns = ['Source', 'Target', 'Weight']

In [ ]:
node_topic = pd.pivot_table((df_merge.loc[df_merge['Topic'].isin(Topic_COP28)]),
                            values=['Name'],
                            index=['Topic'],
                            aggfunc='first'
)

node_topic.reset_index(inplace=True)

In [ ]:
node_topic.columns=['Id', 'Label']

In [ ]:
node_user.columns = ['Id', 'Label', 'categorie']

In [ ]:
df_node=pd.concat([node_topic, node_user])

In [ ]:
df_node.fillna('Topic', inplace=True)

In [ ]:
df_edge.to_csv('/content/drive/MyDrive/network/cop28_edge_topic.csv', sep=',', index=False)

In [ ]:
df_node.to_csv('/content/drive/MyDrive/network/cop28_node_topic.csv', sep=',', index=False)